<a href="https://colab.research.google.com/github/nacha-suk/LLM-ML-OralBioavailability-Predictive-Models/blob/main/src/dissolution_feature_extractor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
import io
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit, fsolve, brentq # brentq was not explicitly used in solvers, fsolve might be an option for complex ones
from sklearn.metrics import mean_squared_error
import inspect # Ensure this is imported
from scipy.interpolate import CubicSpline # Change from PchipInterpolator

# Assuming execution in Colab for `files.upload()` and `files.download()`
try:
    from google.colab import files
except ImportError:
    print("Warning: 'google.colab.files' not found. File operations will be manual if not in Colab.")
    files = None # Placeholder

# --- Model Definitions ---
# Each model function returns Q_predicted at time t with given parameters.
# Q_max is the maximum dissolution, k (or K0, K1 etc.) are rate constants.
# n is release exponent (Korsmeyer-Peppas), a,b,Ti are Weibull params.

def zero_order_model(t, K0, Ti):
    """ Q = K0 * (t - Ti) for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    # For fitting, allow Q to exceed 100 if K0 is large, clipping handled later if needed for prediction.
    return K0 * time_eff

def first_order_model(t, Q_max, K1, Ti):
    """ Q = Q_max * (1 - exp(-K1 * (t - Ti))) for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    return Q_max * (1 - np.exp(-K1 * time_eff))

def second_order_model(t, Q_max, K2, Ti):
    """ Q = (Q_max^2 * K2 * (t-Ti)) / (1 + Q_max * K2 * (t-Ti)) for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    numerator = (Q_max**2) * K2 * time_eff
    denominator = 1 + Q_max * K2 * time_eff
    return np.where(denominator != 0, numerator / denominator, 0)

def higuchi_model(t, KH, Ti):
    """ Q = KH * sqrt(t - Ti) for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    return KH * np.sqrt(time_eff)

def korsmeyer_peppas_model(t, KKP, n, Ti):
    """ Q = KKP * (t - Ti)^n for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    # Add a small epsilon to time_eff if it's zero and n is small to avoid 0^small_n issues if KKP is large
    # However, np.power(0, positive) is 0, which is fine.
    return KKP * np.power(time_eff, n)

def hixson_crowell_model(t, Q_max, KHC, Ti):
    """ Q = Q_max - (Q_max^(1/3) - KHC * (t-Ti))^3 for t >= Ti and KHC*(t-Ti) <= Q_max^(1/3) """
    time_eff = np.maximum(0, t - Ti)
    val_to_cube = Q_max**(1/3) - KHC * time_eff
    # Q should not exceed Q_max, so (Q_max^(1/3) - KHC*t_eff)^3 should be >= 0
    # This means Q_max^(1/3) - KHC*t_eff should be >= 0.
    # If val_to_cube is negative, power(negative, 3) is negative. Q_max - (negative) = Q_max + positive > Q_max.
    # So we clip val_to_cube at 0 before cubing.
    predicted_q = Q_max - np.power(np.maximum(0, val_to_cube), 3)
    return np.minimum(predicted_q, Q_max) # Ensure Q does not exceed Q_max from positive val_to_cube

def weibull_model(t, Q_max, a, b, Ti): # Weibull already includes Ti
    """ Q = Q_max * (1 - exp(-((t - Ti)^b) / a)) for t >= Ti """
    time_eff = np.maximum(0, t - Ti)
    # To prevent overflow with large b and large time_eff, or large a:
    # (time_eff**b) can be very large. exp(-(large)) is 0.
    # If a is very small, (time_eff**b)/a can be very large.
    # np.exp handles large negative exponents by returning 0.
    exponent_val = np.power(time_eff, b) / a
    return Q_max * (1 - np.exp(-exponent_val))


# --- Solvers for T from Q, accounting for Lag Time (Ti) ---
# params for each will now include Ti as the last element

def solve_zero_order(target_q, params): # params = [K0, Ti]
    K0, Ti = params[0], params[1]
    if K0 <= 1e-9: return np.nan # Avoid division by zero or extremely small K0
    if target_q < 0: return np.nan # Cannot have negative dissolution
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    time_eff_solved = target_q / K0
    return Ti + time_eff_solved

def solve_first_order(target_q, params): # params = [Q_max, K1, Ti]
    Q_max, K1, Ti = params[0], params[1], params[2]
    if K1 <= 1e-9 or Q_max <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    if np.isclose(target_q, Q_max): return np.inf # Asymptotically approaches Q_max
    if target_q > Q_max: return np.nan # Cannot exceed Q_max

    val_in_log = 1 - target_q / Q_max
    if val_in_log <= 1e-9: return np.inf # Effectively target_q is Q_max or very close

    time_eff_solved = -np.log(val_in_log) / K1
    if time_eff_solved < -1e-9 : return np.nan # Effective time cannot be negative
    return Ti + np.maximum(0, time_eff_solved)

def solve_second_order(target_q, params): # params = [Q_max, K2, Ti]
    Q_max, K2, Ti = params[0], params[1], params[2]
    if K2 <= 1e-9 or Q_max <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    if np.isclose(target_q, Q_max): return np.inf # Denominator approaches zero
    if target_q > Q_max: return np.nan # Cannot exceed Q_max

    denominator = K2 * Q_max * (Q_max - target_q)
    if denominator <= 1e-9: return np.inf # Effectively target_q is Q_max

    time_eff_solved = target_q / denominator
    if time_eff_solved < -1e-9 : return np.nan
    return Ti + np.maximum(0, time_eff_solved)

def solve_higuchi(target_q, params): # params = [KH, Ti]
    KH, Ti = params[0], params[1]
    if KH <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    time_eff_solved = (target_q / KH)**2
    return Ti + time_eff_solved # time_eff_solved will be >=0

def solve_korsmeyer_peppas(target_q, params): # params = [KKP, n, Ti]
    KKP, n, Ti = params[0], params[1], params[2]
    if KKP <= 1e-9 or n <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    val_for_power = target_q / KKP
    if val_for_power < 0 : return np.nan # Should not happen if target_q > 0, KKP > 0

    time_eff_solved = np.power(val_for_power, 1/n)
    return Ti + time_eff_solved # time_eff_solved should be >=0

def solve_hixson_crowell(target_q, params): # params = [Q_max, KHC, Ti]
    Q_max, KHC, Ti = params[0], params[1], params[2]
    if KHC <= 1e-9 or Q_max <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    if np.isclose(target_q, Q_max): return np.inf # As (Q_max-target_q) approaches 0
    if target_q > Q_max: return np.nan

    term_qmax_minus_q = Q_max - target_q
    # term_qmax_minus_q should be positive here due to checks above

    numerator = Q_max**(1/3) - term_qmax_minus_q**(1/3)
    if numerator < -1e-9 : return np.nan # Should not happen if Q_max > target_q > 0

    time_eff_solved = numerator / KHC
    if time_eff_solved < -1e-9 : return np.nan
    return Ti + np.maximum(0, time_eff_solved)

def solve_weibull(target_q, params): # params = [Q_max, a, b, Ti] (already has Ti)
    Q_max, a, b, Ti = params[0], params[1], params[2], params[3]
    if a <= 1e-9 or b <= 1e-9 or Q_max <= 1e-9: return np.nan
    if target_q < 0: return np.nan
    if np.isclose(target_q, 0): return Ti if Ti >= 0 else 0

    if np.isclose(target_q, Q_max) and target_q >= Q_max : return np.inf # Asymptotically approaches Q_max
    if target_q > Q_max: return np.nan # Cannot exceed Q_max

    val_in_log = 1 - target_q / Q_max
    if val_in_log <= 1e-9: return np.inf # Effectively target_q is Q_max or very close

    base_for_power = a * (-np.log(val_in_log))
    if base_for_power < 0: # Can happen if -np.log(val_in_log) is negative, which it shouldn't be if val_in_log is (0,1)
        return np.nan

    time_eff_solved = np.power(base_for_power, 1/b)
    if np.isnan(time_eff_solved) or time_eff_solved < -1e-9: return np.nan
    return Ti + np.maximum(0, time_eff_solved)

def solve_gompertz(target_q, params): #Q_max, alpha, beta
    Q_max, alpha, beta = params[0], params[1], params[2]
    if Q_max <=0 or alpha <= 0 or beta <= 0: return np.nan
    if target_q <= 0: return 0 # Approximation, Gompertz approaches 0 slowly.
    if target_q >= Q_max * np.exp(-alpha * np.exp(-beta * np.inf)) and target_q >= Q_max : # effectively target_q >= Q_max
        return np.nan # Target Q is at or beyond asymptote

    # Q/Q_max = exp(-alpha * exp(-beta * t))
    # log(Q/Q_max) = -alpha * exp(-beta * t)
    # -log(Q/Q_max)/alpha = exp(-beta * t)
    # log(-log(Q/Q_max)/alpha) = -beta * t
    # t = -log(-log(Q/Q_max)/alpha) / beta
    if target_q / Q_max <=0 : return np.nan
    log_q_qmax = np.log(target_q / Q_max)
    if log_q_qmax >=0 : return np.nan # Means Q >= Q_max

    exp_term_val = -log_q_qmax / alpha
    if exp_term_val <= 0 : return np.nan # Cannot take log

    return -np.log(exp_term_val) / beta

def solve_hopfenberg(target_q, params): #Q_max, KHo
    Q_max, KHo = params[0], params[1]
    if Q_max <= 0 or KHo <=0: return np.nan
    if target_q <=0 : return 0
    if target_q >= Q_max : return np.nan

    # target_q = Q_max * (1 - (1 - KHo * t)^3)
    # target_q/Q_max = 1 - (1 - KHo * t)^3
    # 1 - target_q/Q_max = (1 - KHo * t)^3
    # (1 - target_q/Q_max)^(1/3) = 1 - KHo * t
    # KHo * t = 1 - (1 - target_q/Q_max)^(1/3)
    # t = (1 - (1 - target_q/Q_max)^(1/3)) / KHo
    val_for_root = 1 - target_q/Q_max
    if val_for_root < 0 : return np.nan # should be caught by target_q >= Q_max
    return (1 - val_for_root**(1/3)) / KHo


# --- Existing `load_and_prepare_data_v2` (slightly adapted for clarity if needed) ---
def load_and_prepare_data_v2(
    file_path_or_uploaded_file=None,
    grouping_col_name='In_Vitro_ID',
    time_col_name_options=None,
    dissolution_col_name_options=None
):
    if time_col_name_options is None:
        time_col_name_options = ['Time (min)', 'Time', 'time', 'Minutes', 'Timepoint', 't', 'Time [h]']
    if dissolution_col_name_options is None:
        dissolution_col_name_options = ['% Dissolved', 'Diss [%]', 'Dissolved', 'Percent Dissolved', 'Cumulative Dissolved']

    df = None
    file_identifier = "No file processed"

    if file_path_or_uploaded_file is None:
        print("Warning: No file path or upload object was provided. Using example DataFrame.")
        file_identifier = "example data"
        example_data = {
            'In_Vitro_ID': ['1']*7 + ['2']*6 + ['3']*7 + ['4']*3 + ['5']*7,
            'Time (min)':  [0,10,20,30,45,60,70, 0,15,30,60,90,120, 0,5,10,10,20,30,40, 0,10,20, 0,10,20,30,40,50,50],
            '% Dissolved': [0,15,35,60,85,100,102, 0,20,42,70,95,100, 0,8,20,18,22,30,38, 0,2,5, 0,25,55,80,100,99,100]
        }
        df = pd.DataFrame(example_data)
    elif isinstance(file_path_or_uploaded_file, str):
        file_identifier = file_path_or_uploaded_file
        try:
            df = pd.read_csv(file_path_or_uploaded_file)
            print(f"Successfully loaded '{file_identifier}' from path.")
        except FileNotFoundError:
            print(f"Error: File not found at '{file_identifier}'. Exiting.")
            return None, None, None, None
        except Exception as e:
            print(f"Error loading file '{file_identifier}' from path: {e}. Exiting.")
            return None, None, None, None
    else: # Assumes a Colab uploaded file object
        try:
            filename = list(file_path_or_uploaded_file.keys())[0]
            file_identifier = filename
            print(f"Attempting to load '{file_identifier}' from Colab upload object.")
            df = pd.read_csv(io.BytesIO(file_path_or_uploaded_file[filename]))
            print(f"Successfully loaded '{file_identifier}' from upload object.")
        except Exception as e:
            print(f"Error loading from uploaded file object '{file_identifier}': {e}. Exiting.")
            return None, None, None, None

    if df is None:
        print(f"DataFrame is None for '{file_identifier}'. Exiting.")
        return None, None, None, None

    print(f"\nInitial DataFrame head from '{file_identifier}':")
    print(df.head())

    identified_group_col = None
    if grouping_col_name in df.columns:
        identified_group_col = grouping_col_name
    else: # Try finding a similar column if default is not exact.
        for col in df.columns:
            if grouping_col_name.lower().replace("_","").replace(" ","") == col.lower().replace("_","").replace(" ",""):
                identified_group_col = col
                print(f"Found grouping column '{identified_group_col}' (similar to '{grouping_col_name}')")
                break
    if not identified_group_col:
        print(f"Error: Grouping column '{grouping_col_name}' not found in {df.columns.tolist()}. Exiting.")
        return None, None, None, None
    print(f"Using grouping column: '{identified_group_col}'")


    identified_time_col = next((tc for tc in time_col_name_options if tc in df.columns), None)
    if not identified_time_col:
        print(f"Error: No suitable time column found from options: {time_col_name_options}. Available: {df.columns.tolist()}. Exiting.")
        return None, None, None, None
    print(f"Using time column: '{identified_time_col}'")

    identified_diss_col = next((dc for dc in dissolution_col_name_options if dc in df.columns), None)
    if not identified_diss_col:
        print(f"Error: No suitable dissolution column found from options: {dissolution_col_name_options}. Available: {df.columns.tolist()}. Exiting.")
        return None, None, None, None
    print(f"Using dissolution column: '{identified_diss_col}'")

    df_std = df.rename(columns={
        identified_group_col: 'Profile_ID',
        identified_time_col: 'Time',
        identified_diss_col: 'Dissolved_Percent'
    })

    df_std['Time'] = pd.to_numeric(df_std['Time'], errors='coerce')
    df_std['Dissolved_Percent'] = pd.to_numeric(df_std['Dissolved_Percent'], errors='coerce')

    # Cap dissolution at a reasonable maximum if needed, e.g. 105, if super-saturation is an issue or errors.
    # df_std['Dissolved_Percent'] = np.clip(df_std['Dissolved_Percent'], 0, 105)


    if df_std[['Time', 'Dissolved_Percent']].isnull().any().any():
        print("\nWarning: Non-numeric values found or NaNs present in Time or Dissolved_Percent columns after coercion.")
        print("Rows with NaN values before critical processing:")
        print(df_std[df_std['Time'].isnull() | df_std['Dissolved_Percent'].isnull()])
        df_std.dropna(subset=['Time', 'Dissolved_Percent'], inplace=True)
        print("Rows with NaN values in Time/Dissolved_Percent have been dropped.")

    print(f"\nData using standardized columns: Profile_ID, Time, Dissolved_Percent. Ready for processing.")
    return df_std, 'Profile_ID', 'Time', 'Dissolved_Percent'


def calculate_t_values_from_models(profile_df, target_percentages_list,
                                   add_zero_zero_point=True,
                                   interpolate_profiles=True,
                                   interpolation_target_points=20):
    """
    Fits multiple dissolution models (with Ti) to a single profile,
    selects the best one based on MSE, and calculates T(Q%) values.
    Optionally interpolates profiles with few points using CubicSpline.
    Korsmeyer-Peppas 60% rule for fitting is removed. Allows extrapolation for T(Q%).
    """
    profile_id = profile_df['Profile_ID'].iloc[0]
    log_entries = [f"Profile_ID {profile_id}: Model fitting started."]

    data = profile_df[['Time', 'Dissolved_Percent']].copy()
    data = data.sort_values(by=['Time', 'Dissolved_Percent']).drop_duplicates()

    if add_zero_zero_point:
        if not ((data['Time'] == 0) & (data['Dissolved_Percent'] == 0)).any():
            zero_point = pd.DataFrame({'Time': [0], 'Dissolved_Percent': [0]})
            data = pd.concat([zero_point, data], ignore_index=True)
            data = data.sort_values(by=['Time', 'Dissolved_Percent'])
            data = data.drop_duplicates(subset=['Time'], keep='first')
            log_entries.append("Added (0,0) point and ensured time monotonicity.")

    time_points_orig = data['Time'].values
    diss_points_orig = data['Dissolved_Percent'].values

    # --- Interpolation Step using CubicSpline ---
    if interpolate_profiles and len(time_points_orig) >= 2 and len(time_points_orig) < interpolation_target_points:
        try:
            if len(time_points_orig) < 2:
                 raise ValueError("CubicSpline interpolation requires at least 2 data points.")

            cubic_spline_interpolator = CubicSpline(time_points_orig, diss_points_orig, extrapolate=False)

            min_t, max_t = time_points_orig[0], time_points_orig[-1]
            time_points_interp = np.linspace(min_t, max_t, interpolation_target_points)
            diss_points_interp = cubic_spline_interpolator(time_points_interp)

            q_max_before_interp = diss_points_orig.max() if len(diss_points_orig) > 0 else 0
            # Clip to prevent non-physical values if spline overshoots significantly
            diss_points_interp = np.clip(diss_points_interp, 0, max(105, q_max_before_interp * 1.1)) # Allow 10% overshoot before capping at 105

            log_entries.append(f"Interpolated profile from {len(time_points_orig)} to {len(time_points_interp)} points using CubicSpline.")
            time_points = time_points_interp
            diss_points = diss_points_interp
        except Exception as e_interp:
            log_entries.append(f"Warning: CubicSpline interpolation failed for profile {profile_id}: {e_interp}. Using original points.")
            time_points = time_points_orig
            diss_points = diss_points_orig
    else:
        time_points = time_points_orig
        diss_points = diss_points_orig
        if interpolate_profiles and len(time_points_orig) < 2:
             log_entries.append(f"Skipped interpolation: Profile {profile_id} has < 2 points.")
        elif interpolate_profiles and len(time_points_orig) >= interpolation_target_points:
             log_entries.append(f"Skipped interpolation: Profile {profile_id} already has {len(time_points_orig)} >= {interpolation_target_points} points.")

    q_max_observed = diss_points.max() if len(diss_points) > 0 else 0.0
    if q_max_observed <= 0: q_max_observed = 1.0

    if len(time_points) < 2:
        log_entries.append("Less than 2 unique data points available for fitting. Skipping model fitting.")
        nan_results = pd.Series([np.nan] * len(target_percentages_list), index=[f'T{tp}%' for tp in target_percentages_list])
        nan_results['Best_Model'] = "N/A"
        nan_results['Best_MSE'] = np.nan
        temp_models_param_counts = {
             "Zero-Order": 2, "First-Order": 3, "Second-Order": 3, "Higuchi": 2,
             "Korsmeyer-Peppas": 3, "Hixson-Crowell": 3, "Weibull": 4
        }
        param_cols_to_add = max(temp_models_param_counts.values()) if temp_models_param_counts else 0
        for i in range(1, param_cols_to_add + 1):
            nan_results[f'Param_{i}'] = np.nan
        return nan_results, "\n".join(log_entries)

    # Helper for Ti p0: tries to use first time point if dissolution is near zero there, else small fraction of max time
    def get_ti_p0(t_fit, q_fit_for_ti_logic):
        if len(t_fit) > 0:
            first_diss_val = q_fit_for_ti_logic[0] if len(q_fit_for_ti_logic) > 0 else 1.0 # Default to 1 if q_fit is empty
            if t_fit[0] > 1e-3 and first_diss_val < 1e-2 : # If first timepoint is not zero and diss is very low
                return t_fit[0] * 0.9 # Guess Ti is close to the first time point
            if t_fit[-1] > 0:
                return t_fit[-1] / 20 # Else, small fraction of max time
        return 0.01 # Default small Ti

    get_ti_upper_bound = lambda t_fit: (t_fit[-1] / 1.5 if len(t_fit) > 0 and t_fit[-1] > 0 else 1.0) # Ti not more than 2/3 of total time

    def create_general_bounds_func_with_ti(default_lower_kinetics, default_upper_kinetics, qmax_idx_in_params=0, has_qmax=True):
        def bounds_func(t, q, qm_obs):
            lower_b = list(default_lower_kinetics) + [0]
            upper_b = list(default_upper_kinetics) + [get_ti_upper_bound(t)]

            if has_qmax and qmax_idx_in_params < len(default_lower_kinetics):
                lower_b[qmax_idx_in_params] = max(0, qm_obs * 0.8)
                upper_b[qmax_idx_in_params] = max(qm_obs * 1.01, 1.0)
                if upper_b[qmax_idx_in_params] > 150: upper_b[qmax_idx_in_params] = 150
            return (lower_b, upper_b)
        return bounds_func

    weibull_p0_func = lambda t, q, qm_obs: [
        qm_obs, 10, 1, get_ti_p0(t,q)
    ]
    weibull_bounds_func = lambda t, q, qm_obs: (
        [max(0, qm_obs * 0.8), 1e-6, 1e-6, 0],
        [max(qm_obs * 1.01, 1.0, 150 if qm_obs*1.01 > 150 else qm_obs*1.01), np.inf, 10, get_ti_upper_bound(t)]
    )

    models_config = {
        "Zero-Order": {"func": zero_order_model, "solver": solve_zero_order, "params": 2,
                       "p0_func": lambda t,q,qm_obs: [qm_obs/(t[-1]-get_ti_p0(t,q)) if len(t)>0 and (t[-1]-get_ti_p0(t,q))>1e-6 else 1.0, get_ti_p0(t,q)],
                       "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[1e-6], default_upper_kinetics=[np.inf], has_qmax=False)},
        "First-Order": {"func": first_order_model, "solver": solve_first_order, "params": 3,
                        "p0_func": lambda t,q,qm_obs: [qm_obs, 0.1, get_ti_p0(t,q)],
                        "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[0, 1e-6], default_upper_kinetics=[150, np.inf], qmax_idx_in_params=0)},
        "Second-Order": {"func": second_order_model, "solver": solve_second_order, "params": 3,
                         "p0_func": lambda t,q,qm_obs: [qm_obs, 0.01, get_ti_p0(t,q)],
                         "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[0, 1e-6], default_upper_kinetics=[150, np.inf], qmax_idx_in_params=0)},
        "Higuchi": {"func": higuchi_model, "solver": solve_higuchi, "params": 2,
                    "p0_func": lambda t,q,qm_obs: [qm_obs/np.sqrt(t[-1]-get_ti_p0(t,q)) if len(t)>0 and (t[-1]-get_ti_p0(t,q))>1e-6 else 1.0, get_ti_p0(t,q)],
                    "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[1e-6], default_upper_kinetics=[np.inf], has_qmax=False)},
        "Korsmeyer-Peppas": {"func": korsmeyer_peppas_model, "solver": solve_korsmeyer_peppas, "params": 3,
                             "p0_func": lambda t,q,qm_obs: [10, 0.5, get_ti_p0(t,q)],
                             "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[1e-6, 1e-6], default_upper_kinetics=[np.inf, 5], has_qmax=False)},
        "Hixson-Crowell": {"func": hixson_crowell_model, "solver": solve_hixson_crowell, "params": 3,
                           "p0_func": lambda t,q,qm_obs: [qm_obs, 0.01, get_ti_p0(t,q)],
                           "bounds_func": create_general_bounds_func_with_ti(default_lower_kinetics=[0, 1e-6], default_upper_kinetics=[150, np.inf], qmax_idx_in_params=0)},
        "Weibull": {"func": weibull_model, "solver": solve_weibull, "params": 4,
                    "p0_func": weibull_p0_func,
                    "bounds_func": weibull_bounds_func},
    }

    best_model_name = None
    best_mse = np.inf
    best_params = None
    max_params_count = 0
    if models_config:
        for _, model_info_loop in models_config.items():
            if model_info_loop.get("params",0) > max_params_count:
                max_params_count = model_info_loop.get("params",0)

    for name, model_info in models_config.items():
        current_time_points_fitting = time_points
        current_diss_points_fitting = diss_points

        if len(current_time_points_fitting) < model_info["params"]:
            log_entries.append(f"Skipping {name}: Not enough data points ({len(current_time_points_fitting)}) for {model_info['params']} parameters after interpolation attempt.")
            continue

        try:
            effective_qm_for_p0 = q_max_observed if q_max_observed > 1.0 else 100.0
            # Pass current_diss_points_fitting to p0_func for Ti logic
            p0 = model_info["p0_func"](current_time_points_fitting, current_diss_points_fitting, effective_qm_for_p0)


            if "bounds_func" in model_info:
                actual_bounds_lists = model_info["bounds_func"](current_time_points_fitting, current_diss_points_fitting, q_max_observed)
            else:
                actual_bounds_lists = [list(b) for b in model_info["bounds"]]

            for i_param in range(len(p0)):
                current_p0_val = p0[i_param]
                if isinstance(current_p0_val, (list, np.ndarray)): current_p0_val = current_p0_val[0]

                lower_bound_val = actual_bounds_lists[0][i_param]
                upper_bound_val = actual_bounds_lists[1][i_param]

                # Ensure p0 is not exactly on the bound if possible, or that bounds are wide enough
                if upper_bound_val - lower_bound_val < 1e-7: # If bounds are extremely tight
                    p0[i_param] = lower_bound_val # Set to lower bound
                elif current_p0_val <= lower_bound_val: p0[i_param] = lower_bound_val + 1e-7 if lower_bound_val + 1e-7 < upper_bound_val else lower_bound_val
                elif current_p0_val >= upper_bound_val: p0[i_param] = upper_bound_val - 1e-7 if upper_bound_val - 1e-7 > lower_bound_val else upper_bound_val
                else: p0[i_param] = current_p0_val


            final_bounds_tuple = (np.array(actual_bounds_lists[0]), np.array(actual_bounds_lists[1]))

            if len(p0) != len(final_bounds_tuple[0]) or len(p0) != len(final_bounds_tuple[1]):
                log_entries.append(f"Skipping {name}: Mismatch in p0/bounds length. p0: {p0} ({len(p0)}), bounds_low: {final_bounds_tuple[0]} ({len(final_bounds_tuple[0])}), bounds_high: {final_bounds_tuple[1]} ({len(final_bounds_tuple[1])})")
                continue

            # Ensure p0 is strictly within bounds for 'trf' and 'dogbox'
            for i_check in range(len(p0)):
                if not (final_bounds_tuple[0][i_check] <= p0[i_check] <= final_bounds_tuple[1][i_check]):
                    p0[i_check] = np.clip(p0[i_check], final_bounds_tuple[0][i_check], final_bounds_tuple[1][i_check])
                    # If bounds are equal, clip might not put it strictly inside.
                    if final_bounds_tuple[0][i_check] == final_bounds_tuple[1][i_check]:
                         p0[i_check] = final_bounds_tuple[0][i_check]
                    elif p0[i_check] <= final_bounds_tuple[0][i_check]:
                        p0[i_check] = final_bounds_tuple[0][i_check] + 1e-8 # Push slightly off boundary
                    elif p0[i_check] >= final_bounds_tuple[1][i_check]:
                        p0[i_check] = final_bounds_tuple[1][i_check] - 1e-8 # Push slightly off boundary
                # Ensure lower bound is less than upper bound
                if final_bounds_tuple[0][i_check] > final_bounds_tuple[1][i_check]:
                    raise ValueError(f"Lower bound > Upper bound for param {i_check} in model {name}")


            params, covariance = curve_fit(
                model_info["func"],
                current_time_points_fitting,
                current_diss_points_fitting,
                p0=p0,
                bounds=final_bounds_tuple,
                maxfev=10000, # Increased from 5000 previously
                method='trf',
                ftol=1e-7, xtol=1e-7, gtol=1e-7 # Adjusted tolerances
            )
            predicted_diss_fitting = model_info["func"](current_time_points_fitting, *params)
            mse = mean_squared_error(current_diss_points_fitting, predicted_diss_fitting)

            log_entries.append(f"Fit {name}: MSE={mse:.4e}, Params={np.round(params,4)}")

            if mse < best_mse:
                best_mse = mse
                best_model_name = name
                best_params = params
        except RuntimeError as re:
            log_entries.append(f"Could not fit {name}: RuntimeError ({re}).")
        except ValueError as ve:
            log_entries.append(f"Could not fit {name}: ValueError ({ve}). Check p0/bounds. p0={p0 if 'p0' in locals() else 'p0_not_set'}, bounds={final_bounds_tuple if 'final_bounds_tuple' in locals() else 'bounds_not_set'}")
        except Exception as e:
            log_entries.append(f"Could not fit {name}: Unexpected Error {type(e).__name__} ({e})")

    results_s = pd.Series(index=[f'T{tp}%' for tp in target_percentages_list], dtype=float)
    if best_model_name:
        log_entries.append(f"Best Model for Profile {profile_id}: {best_model_name} with MSE={best_mse:.4e}, Params={np.round(best_params,4) if best_params is not None else 'None'}")
        solver_func = models_config[best_model_name]["solver"]

        for tp in target_percentages_list:
            if best_params is None:
                results_s[f'T{tp}%'] = np.nan
                continue

            if tp == 0:
                ti_val = 0.0
                if len(best_params) > 0 :
                    ti_param_val = best_params[-1]
                    ti_val = ti_param_val if ti_param_val > 1e-4 else 0.0
                results_s[f'T{tp}%'] = ti_val
                continue

            try:
                t_val = solver_func(tp, best_params)
                results_s[f'T{tp}%'] = t_val if t_val is not None and np.isfinite(t_val) else np.nan
            except Exception as e_solve:
                results_s[f'T{tp}%'] = np.nan
                log_entries.append(f"Error solving T{tp}% for {best_model_name}: {type(e_solve).__name__} ({e_solve})")

        results_s['Best_Model'] = best_model_name
        results_s['Best_MSE'] = best_mse
        if best_params is not None:
            for i, p_val in enumerate(best_params):
                results_s[f'Param_{i+1}'] = p_val
            for i in range(len(best_params), max_params_count):
                results_s[f'Param_{i+1}'] = np.nan
        else:
            for i in range(1, max_params_count + 1): results_s[f'Param_{i}'] = np.nan
    else:
        log_entries.append(f"No suitable model could be fit for Profile {profile_id}.")
        results_s['Best_Model'] = "N/A"
        results_s['Best_MSE'] = np.nan
        for i in range(1, max_params_count + 1):
             results_s[f'Param_{i}'] = np.nan

    return results_s, "\n".join(log_entries)

def plot_dissolution_model_fits(df_orig, model_results_df, profile_id_col='Profile_ID',
                                time_col='Time', dissolution_col='Dissolved_Percent',
                                # num_profiles_to_plot=5, # <<< REMOVE THIS PARAMETER
                                interpolate_profiles=True,
                                interpolation_target_points=20):
    """
    Plots original dissolution data, CubicSpline interpolated points (if used for fitting),
    and the best-fit model curve for ALL profiles.
    """
    unique_profiles = df_orig[profile_id_col].unique()
    # actual_profiles_to_plot = unique_profiles[:min(len(unique_profiles), num_profiles_to_plot)] # <<< OLD LINE
    actual_profiles_to_plot = unique_profiles # <<< CHANGE THIS LINE to plot all

    if not actual_profiles_to_plot.any():
        print("No profiles to plot.")
        return

    num_cols = 2 # You might want to adjust this for better layout if many profiles (e.g., 3 or 4)
    num_rows = (len(actual_profiles_to_plot) + num_cols - 1) // num_cols

    # Consider adjusting figsize if you anticipate a very large number of plots
    # For example, you could cap the individual plot size or make the overall figure even larger.
    # Current figsize scales with the number of plots.
    fig, axes = plt.subplots(num_rows, num_cols, figsize=(8 * num_cols, 6 * num_rows), squeeze=False)
    axes = axes.flatten()

    # ... (rest of the function remains the same) ...

    # Model functions for plotting the curve (ensure these are defined in your script)
    model_funcs = {
        "Zero-Order": zero_order_model, "First-Order": first_order_model,
        "Second-Order": second_order_model, "Higuchi": higuchi_model,
        "Korsmeyer-Peppas": korsmeyer_peppas_model, "Hixson-Crowell": hixson_crowell_model,
        "Weibull": weibull_model
    }

    for i, profile_id_val in enumerate(actual_profiles_to_plot):
        ax = axes[i]
        profile_data_orig = df_orig[df_orig[profile_id_col] == profile_id_val]

        ax.scatter(profile_data_orig[time_col], profile_data_orig[dissolution_col],
                   label=f'Original Points (ID: {profile_id_val})', s=50, alpha=0.9, zorder=3, color='blue')

        time_points_orig_profile = profile_data_orig[time_col].values
        diss_points_orig_profile = profile_data_orig[dissolution_col].values

        if interpolate_profiles and len(time_points_orig_profile) >= 2 and len(time_points_orig_profile) < interpolation_target_points:
            try:
                cubic_spline_interpolator = CubicSpline(time_points_orig_profile, diss_points_orig_profile, extrapolate=False)
                min_t, max_t = time_points_orig_profile[0], time_points_orig_profile[-1]
                time_points_interp_plot = np.linspace(min_t, max_t, interpolation_target_points)
                diss_points_interp_plot = cubic_spline_interpolator(time_points_interp_plot)

                q_max_before_interp = diss_points_orig_profile.max() if len(diss_points_orig_profile) > 0 else 0
                diss_points_interp_plot = np.clip(diss_points_interp_plot, 0, max(105, q_max_before_interp * 1.1))

                ax.scatter(time_points_interp_plot, diss_points_interp_plot,
                           label=f'CubicSpline Points (Fit Target: {interpolation_target_points})',
                           s=15, alpha=0.7, zorder=2, color='green', marker='x')
            except Exception as e_interp_plot:
                print(f"Note: Could not generate/plot spline points for profile {profile_id_val} due to: {e_interp_plot}")

        current_model_results_df = model_results_df
        if current_model_results_df.index.name != profile_id_col:
            if profile_id_col in current_model_results_df.columns:
                current_model_results_df = current_model_results_df.set_index(profile_id_col)
            else:
                print(f"Warning: Profile ID column '{profile_id_col}' not found in model_results_df index or columns for plotting.")

        if profile_id_val in current_model_results_df.index:
            profile_model_info = current_model_results_df.loc[profile_id_val]

            if pd.notna(profile_model_info.get('Best_Model')) and profile_model_info['Best_Model'] != "N/A":
                best_model_name = profile_model_info['Best_Model']

                num_expected_params = 0
                j=1
                while f'Param_{j}' in profile_model_info and pd.notna(profile_model_info[f'Param_{j}']):
                    num_expected_params +=1
                    j+=1

                if num_expected_params > 0 :
                    model_params = [profile_model_info[f'Param_{k+1}'] for k in range(num_expected_params)]

                    if best_model_name in model_funcs:
                        model_function_to_plot = model_funcs[best_model_name]

                        t_plot_min = profile_data_orig[time_col].min()
                        t_plot_max = profile_data_orig[time_col].max()

                        ti_param_idx = -1
                        try:
                            model_signature_args = inspect.getfullargspec(model_function_to_plot).args
                            if "Ti" in model_signature_args:
                                ti_param_idx = len(model_params) -1
                        except: pass

                        if ti_param_idx != -1 and len(model_params) > ti_param_idx and model_params[ti_param_idx] > t_plot_min :
                                t_plot_min = min(t_plot_min, model_params[ti_param_idx] * 0.9)

                        t_plot_curve = np.linspace(t_plot_min, t_plot_max, 200)
                        q_predicted_plot_curve = model_function_to_plot(t_plot_curve, *model_params)
                        q_predicted_plot_curve = np.clip(q_predicted_plot_curve, 0, 120)

                        ax.plot(t_plot_curve, q_predicted_plot_curve,
                                label=f'Best Fit: {best_model_name}\nMSE: {profile_model_info["Best_MSE"]:.2e}',
                                linestyle='--', zorder=1, color='red', linewidth=2)
                    else:
                       ax.text(0.5, 0.5, f'Model function for {best_model_name} not in plot list.', horizontalalignment='center', verticalalignment='center', transform=ax.transAxes, fontsize=9)
                else:
                   ax.text(0.5, 0.5, 'No model parameters found for plotting.', horizontalalignment='center', verticalalignment='center', transform=ax.transAxes, fontsize=9)
        else:
            ax.text(0.5, 0.5, f'No model results for profile {profile_id_val}.', horizontalalignment='center', verticalalignment='center', transform=ax.transAxes, fontsize=9)

        ax.set_xlabel('Time')
        ax.set_ylabel('% Dissolved')
        ax.set_title(f'Profile ID: {profile_id_val}')
        ax.legend(fontsize='small')
        ax.grid(True, linestyle=':', alpha=0.7)
        ax.set_ylim(bottom=-5, top=max(105, profile_data_orig[dissolution_col].max()*1.1 + 5 if not profile_data_orig[dissolution_col].empty else 105))
        ax.set_xlim(left= (profile_data_orig[time_col].min() if not profile_data_orig[time_col].empty else 0) - \
                         (profile_data_orig[time_col].max()*0.05 if not profile_data_orig[time_col].empty and profile_data_orig[time_col].max()>0 else 0.1) )

    for j_ax in range(i + 1, len(axes)): # Clean up unused subplots
        fig.delaxes(axes[j_ax])

    plt.tight_layout()
    plt.show()
    # If the figure is too large or you want to save it:
    # plt.savefig("all_profile_fits.png", dpi=300)
    # plt.close(fig) # Close the figure if you saved it and don't need to show it

# --- Main Execution ---
if __name__ == "__main__":
    # --- Configuration ---
    GROUPING_COLUMN = 'In_Vitro_ID'
    TIME_COL_OPTIONS = None
    DISS_COL_OPTIONS = None
    TARGET_PERCENTAGES = np.array([0, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50, 60, 70, 80, 90, 100])
    ADD_ZERO_ZERO = True
    # NUM_PROFILES_TO_PLOT = 6 # <<< YOU CAN REMOVE OR COMMENT OUT THIS LINE

    INTERPOLATE_PROFILES_FLAG = True
    INTERPOLATION_TARGET_POINTS_COUNT = 20

    # ... (Data Loading logic remains the same) ...
    df_main = None
    GRP_COL_STD = None
    profile_specific_logs_list = []

    # (Your existing data loading logic here)
    if files:
        print("Please upload your dissolution data CSV file for model-based analysis:")
        try:
            uploaded_files = files.upload()
            if not uploaded_files:
                raise ValueError("No file uploaded.")
            df_main, GRP_COL_STD, _, _ = load_and_prepare_data_v2(
                file_path_or_uploaded_file=uploaded_files,
                grouping_col_name=GROUPING_COLUMN,
                time_col_name_options=TIME_COL_OPTIONS,
                dissolution_col_name_options=DISS_COL_OPTIONS
            )
        except (NameError, ValueError, ImportError) as e:
            print(f"Colab upload functionality issue or no file uploaded: {e}.")
            print("Falling back to using example data.")
            df_main, GRP_COL_STD, _, _ = load_and_prepare_data_v2(
                file_path_or_uploaded_file=None,
                grouping_col_name='In_Vitro_ID',
            )
    else:
        print("Not in Colab environment. Using example data.")
        df_main, GRP_COL_STD, _, _ = load_and_prepare_data_v2(
            file_path_or_uploaded_file=None,
            grouping_col_name='In_Vitro_ID',
        )

    if df_main is not None and GRP_COL_STD is not None:
        print(f"\n--- Processing Profiles (Model-Based) ---")
        # ... (rest of processing and saving logic) ...
        print(f"Target Percentages for T(Q%): {TARGET_PERCENTAGES}")
        print(f"Add (0,0) Point if missing: {ADD_ZERO_ZERO}")
        print(f"Interpolate profiles with < {INTERPOLATION_TARGET_POINTS_COUNT} points: {INTERPOLATE_PROFILES_FLAG}")
        print(f"Grouping data by standardized column: '{GRP_COL_STD}' (original may vary)\n")

        def process_group_for_models(grp_df):
            results_series, log_str = calculate_t_values_from_models(
                grp_df,
                TARGET_PERCENTAGES,
                add_zero_zero_point=ADD_ZERO_ZERO,
                interpolate_profiles=INTERPOLATE_PROFILES_FLAG,
                interpolation_target_points=INTERPOLATION_TARGET_POINTS_COUNT
            )
            profile_id_for_log = grp_df[GRP_COL_STD].iloc[0]
            profile_specific_logs_list.append(f"--- Log for Profile_ID: {profile_id_for_log} ---\n{log_str}\n")
            print(f"\n--- Log for Profile_ID: {profile_id_for_log} ---")
            print(log_str)
            return results_series

        all_profiles_model_features = df_main.groupby(GRP_COL_STD, group_keys=False).apply(process_group_for_models)

        print("\n--- Transformed Data (Model-Based T(Q%) and Fit Info) ---")
        if isinstance(all_profiles_model_features.index, pd.MultiIndex):
            all_profiles_model_features = all_profiles_model_features.reset_index(level=1, drop=True)
        if all_profiles_model_features.index.name == GRP_COL_STD :
            all_profiles_model_features = all_profiles_model_features.reset_index()
        print(all_profiles_model_features.head())

        output_filename_models = 'dissolution_model_features_and_TQ.csv'
        try:
            all_profiles_model_features.to_csv(output_filename_models, index=False)
            print(f"\nTransformed data saved to '{output_filename_models}'")
            if files:
                try: files.download(output_filename_models)
                except Exception as e_dl: print(f"File download error: {e_dl}")
        except Exception as e_save: print(f"Error saving CSV: {e_save}")

        log_output_filename_models = 'dissolution_model_processing_logs.txt'
        try:
            with open(log_output_filename_models, 'w') as f:
                f.write("\n".join(profile_specific_logs_list))
            print(f"\nProcessing logs saved to '{log_output_filename_models}'")
            if files:
                try: files.download(log_output_filename_models)
                except Exception as e_dl_log: print(f"Log download error: {e_dl_log}")
        except Exception as e_save_log: print(f"Error saving log: {e_save_log}")


        print("\n--- Plotting Model Fits for ALL Profiles ---") # Updated print statement
        plot_dissolution_model_fits(
            df_main,
            all_profiles_model_features,
            profile_id_col=GRP_COL_STD,
            time_col='Time',
            dissolution_col='Dissolved_Percent',
            # num_profiles_to_plot=NUM_PROFILES_TO_PLOT, # <<< REMOVE THIS ARGUMENT
            interpolate_profiles=INTERPOLATE_PROFILES_FLAG,
            interpolation_target_points=INTERPOLATION_TARGET_POINTS_COUNT
        )
    else:
        print(f"\nData loading or preparation failed. No analysis performed.")

Please upload your dissolution data CSV file for model-based analysis:


Saving LLM_dissolution_longformat.csv to LLM_dissolution_longformat (3).csv
Attempting to load 'LLM_dissolution_longformat (3).csv' from Colab upload object.
Successfully loaded 'LLM_dissolution_longformat (3).csv' from upload object.

Initial DataFrame head from 'LLM_dissolution_longformat (3).csv':
   In_Vitro_ID  Time [h]  Diss [%]
0            1      0.00       0.0
1            1      0.08       5.0
2            1      0.25      10.0
3            1      0.50      11.5
4            1      0.75      12.0
Using grouping column: 'In_Vitro_ID'
Using time column: 'Time [h]'
Using dissolution column: 'Diss [%]'

Data using standardized columns: Profile_ID, Time, Dissolved_Percent. Ready for processing.

--- Processing Profiles (Model-Based) ---
Target Percentages for T(Q%): [  0   5  10  15  20  25  30  35  40  45  50  60  70  80  90 100]
Add (0,0) Point if missing: True
Interpolate profiles with < 20 points: True
Grouping data by standardized column: 'Profile_ID' (original may vary)


--

<ipython-input-4-2674001572>:174: RuntimeWarning: overflow encountered in power
  time_eff_solved = np.power(base_for_power, 1/b)



--- Log for Profile_ID: 38 ---
Profile_ID 38: Model fitting started.
Interpolated profile from 6 to 20 points using CubicSpline.
Fit Zero-Order: MSE=6.2604e-02, Params=[ 0.039 16.   ]
Fit First-Order: MSE=2.4619e-02, Params=[ 0.3356 10.6223  0.    ]
Fit Second-Order: MSE=2.4620e-02, Params=[3.356000e-01 4.317901e+02 0.000000e+00]
Fit Higuchi: MSE=6.4020e-02, Params=[ 0.0783 14.9149]
Fit Korsmeyer-Peppas: MSE=1.7251e-02, Params=[0.2476 0.     0.    ]
Fit Hixson-Crowell: MSE=4.1844e-02, Params=[0.3356 0.0166 0.    ]
Fit Weibull: MSE=1.7251e-02, Params=[0.9891 3.4715 0.     0.    ]
Best Model for Profile 38: Weibull with MSE=1.7251e-02, Params=[0.9891 3.4715 0.     0.    ]

--- Log for Profile_ID: 39 ---
Profile_ID 39: Model fitting started.
Interpolated profile from 6 to 20 points using CubicSpline.
Fit Zero-Order: MSE=1.4432e+03, Params=[36.6391  0.    ]
Fit First-Order: MSE=2.7974e+00, Params=[1.011656e+02 3.183700e+00 1.910000e-02]
Fit Second-Order: MSE=2.5458e+00, Params=[1.04374e+0

<ipython-input-4-2674001572>:784: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  all_profiles_model_features = df_main.groupby(GRP_COL_STD, group_keys=False).apply(process_group_for_models)


...

<IPython.core.display.Javascript object>


Processing logs saved to 'dissolution_model_processing_logs.txt'


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>


--- Plotting Model Fits for ALL Profiles ---
